# Load local version of dataset

In [1]:
import datetime as dt
import os

import altair as alt
import quilt3
import pandas as pd

In [2]:
df = pd.read_parquet("urchins2006-2019.parquet")

In [3]:
df['Species'].value_counts()

purple urchin     11599
crowned urchin    11599
red urchin        11599
Name: Species, dtype: int64

In [4]:
df['Site'].value_counts()

Coral St Lucus Pt    900
Breakwater           900
Casino Point         864
Middle Reef          828
Gerstle Cove         792
                    ... 
Flat Iron Rock        18
Monument              18
Timber Cove           18
Fry's Anchorage       18
Asilomar              18
Name: Site, Length: 141, dtype: int64

In [5]:
df['Transect'].value_counts()

2    5802
6    5799
5    5799
4    5799
3    5799
1    5799
Name: Transect, dtype: int64

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 34797 entries, 6 to 132063
Data columns (total 10 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   Site       34797 non-null  object 
 1   Day        34797 non-null  int64  
 2   Month      34797 non-null  int64  
 3   Year       34797 non-null  int64  
 4   Transect   34797 non-null  int64  
 5   Species    34797 non-null  object 
 6   Amount     34647 non-null  float64
 7   Latitude   34797 non-null  float64
 8   Longitude  34797 non-null  float64
 9   Datetime   34797 non-null  object 
dtypes: float64(3), int64(4), object(3)
memory usage: 2.9+ MB


In [7]:
df['Datetime'] = pd.to_datetime(df['Datetime'])

In [12]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

# Initial data plots (using iPython Vega)

In [13]:
source = alt.topo_feature("CA-06-california-counties.json", "cb_2015_california_county_20m")
background = alt.Chart(source).mark_geoshape(
        fill='lightgray',
        stroke='white',
    ).project(
        'albersUsa',
    ).properties(
        width=500,
        height=500,
    )

In [16]:
year_dropdown = alt.binding_select(
    options=[2006,2007,2008,2009]
)

# A slider filter
year_slider = alt.binding_range(min=2006, max=2019, step=1, name="Year")
slider_selection = alt.selection_single(
    bind=year_slider,
    fields=['Year'],
    name="Year"
)

urchins = alt.Chart(df).mark_point(strokeWidth=1, opacity=.2).encode(
    longitude='Longitude:Q',
    latitude='Latitude:Q',
    size='Amount:Q',
    tooltip=['Site:N', 'Species:N', 'Amount:Q'],
    color='Species:N',
).add_selection(
    slider_selection,
    #dropdown_selection
).transform_filter(
    slider_selection
)

final_chart = background + urchins

In [17]:
final_chart

alt.LayerChart(...)

In [11]:
final_chart.save("urchins-interactive.json")